# Using a robust data pipelining tool in R to build a reproducible hurricane data visualization with multi-agency water data

## Context
### Purpose
The purpose is to demonstrate how to use the `targets` R package to construct a reproducible data pipeline that integrates and analyzes data from diverse environmental sources to investigate flooding during Hurricane Harvey, which first made landfall in south-central Texas on August 25, 2017 as a category 4 hurricane.

### Description
The main features of this use case involve fetching, integrating/processing and visualizing time-series data from three distinct public sources: USGS (United States Geoleogical Survey) stream water level (also referred to as gage or stage) data, NWS (National Weather Service) flood stage data, and NHC (National Hurricane Center) storm track data for Hurricane Harvey. The pipeline will ensure that any changes in the raw data or processing functions only trigger a rerun of the necessary downstream steps, promoting efficiency and reproducibility.

### Highlights
- Fetch and integrate diverse data: USGS stage, NWS flood, and NHC storm track data.
- Automate data workflow: Use `targets` for a structured and reproducible workflow.
- Investigate flood event: Focus analysis on the timing and magnitude of flooding during Hurricane Harvey.
- Efficient updates: Only rerun parts of the pipeline affected by data or code changes.

This tutorial is extended from materials and insights shared by Abner Bogan and Lindsay Platt, Environmental Data Scientists at the Consortium of Universities for the Advancement of Hydrologic Science, Inc. (CUAHSI), for the Earth Science Information Partners (ESIP) community. For more detail on this topic, you can read the original post:
[Guest Blog: Reproducible data pipelines in R with {targets}](https://www.esipfed.org/guest-blog-reproducible-data-pipelines-in-r-with-targets/).

## Load libraries

In [1]:
# load the targets library
library(targets)
# load the magick library for displaying static images
library(magick)
# suppress warnings
options(warn = -1)

## Inspect and run pipeline

### Visualizing the Pipeline Network

A key advantage of `targets` is the ability to easily visualize the workflow. This interactive graph (generated by `tar_visnetwork()`) clearly shows how each "target" (data output or derived product) depends on the previous steps and functions. This transparency is crucial for collaboration and maintaining complex projects.

In [ ]:
# this is an interactive graphic showing the pipeline network
tar_visnetwork()

### Running the Pipeline: The First Build

To execute the entire workflow, we use the `tar_make()` command.

The first time `tar_make()` is run, it executes every target (downloading data, processing, and generating the final graphics). Unlike a single R script that must be re-executed entirely, targets intelligently checks the status of every component (data, code, and dependencies) for changes. All `targets` pipeline artifacts are stored in the local cache (`_targets` folder) which is crucial for not only highly efficient re-runs, but for debugging as well.

In [2]:
# execute the pipeline; all targets will run for the first time
tar_make()

+ p1_site_info dispatched
Requesting:
https://api.waterdata.usgs.gov/ogcapi/v0/collections/monitoring-locations/items?f=json&lang=en-US&limit=10000
✔ p1_site_info completed [2.7s, 3.11 kB]
+ p1_nws_table dispatched
Rows: 827 Columns: 7
── Column specification ────────────────────────────────────────────────────────
Delimiter: "|"
chr (7): X1, X2, X3, X4, X5, X6, X7

ℹ Use `spec()` to retrieve the full column specification for this data.
ℹ Specify the column types or set `show_col_types = FALSE` to quiet this message.
Rows: 268 Columns: 7
── Column specification ────────────────────────────────────────────────────────
Delimiter: "|"
chr (7): X1, X2, X3, X4, X5, X6, X7

ℹ Use `spec()` to retrieve the full column specification for this data.
ℹ Specify the column types or set `show_col_types = FALSE` to quiet this message.
✔ p1_nws_table completed s, 36.57 kB]
+ p1_site_data dispatched
Requesting:
https://api.waterdata.usgs.gov/ogcapi/v0/collections/daily/items?f=json&lang=en-US&time=2017-

### Inspect pipeline outputs

To see the final products of our workflow -- namely the hurricane and gage height/flooding stage visualizations, we use the `tar_read()` function, where the input arguement is the name of the target that we are interested in returning. Note that we used a prefix indicating the workflow phase number for both the targets in this pipeline (e.g., `p1_site_data`, `p2_harvey_pts`,`p3_leaflet_map`) along with the folders in this workspace (e.g., `01_fetch`, `02_process`, `03_visualize`).

In [5]:
# this target represents the interactive leaflet map showing the hurricane track over time along with the USGS gage sites for reference
tar_read(p3_leaflet_map)
# this target represents the plot made with ggplot showing the gage height over time (hydrograph) in blue along with the minor flood stage data for reference in red across all analyzed USGS gage sites
tar_read(p3_hydrograph_plot)

HTML widgets cannot be represented in plain text (need html)

### Making Updates and Leveraging Rebuild Capabilities

One of the most powerful features of `targets` is its ability to handle changes efficiently. If this entire analysis were written in a single script, changing one input parameter (e.g., the site ID or a filter date) would force you to re-run the entire script, requiring a full re-download and re-process of all raw data.

With `targets`, only the targets that are affected by the upstream change are re-run. The results of all unaffected steps are loaded instantly from the cache. This efficient rebuild capability saves significant time, computational resources, and unnecessary network bandwidth.

This emphasis on linkages and rebuild capabilities is the main benefit of using a `targets` pipeline over a monolithic script.

#### Example: Simulating a Workflow Update

To demonstrate, let's simulate a change in an input parameter. For instance, imagine we change the input USGS gage sites parameter (represented by `harvey_sites` in the `_targets.R` file) to look at another nearby gage.

In [7]:
# show edits to _targets.R file
image_read('images/workflow_updates.png')

HTML widgets cannot be represented in plain text (need html)

Since we cannot edit the underlying `_targets.R` file interactively here, we will use the `tar_invalidate()` function to force the re-run of the targets associated with the `harvey_sites` object defined in the `_targets.R` to simulate a change in its dependency. Then, we will run `tar_visnetwork()` and `tar_make()` again.

In [ ]:
# simulate a change by invalidating a key object defined in the _targets.R main script outlining the receipe for the pipeline; this tells `targets` that the downstream dependencies need to be rebuilt.
# we need to explicity invalidate the p1_site_data target as well to simulate this change
tar_invalidate(c('harvey_sites','p1_site_data'))
# visualize the workflow
tar_visnetwork()
# run the pipeline again
tar_make()

Notice that the output from the second `tar_make()` call only executes a subset of the total targets. The targets that were unaffected (like the National Hurricane Center data download, which doesn't depend on the USGS site ID) are loaded directly from the cache.

This is the core benefit of using `targets`: a robust, efficient, and reproducible data workflow that rebuilds only what is necessary.

## Summary
- We leveraged the `targets` R package to build a reproducible data pipeline for a complex environmental analysis.
- The analysis integrated diverse water data sources across multiple agencies related to Hurricane Harvey flooding, including USGS stage data, NWS flooding data, and NHC hurricane track data.
- We demonstrated how `targets` tracks dependencies to ensure that only the steps ("targets") affected by changes in code or data are efficiently rebuilt, saving time and reducing errors.
- The modular structure of the `targets` pipeline, using separate functions and organized files, was shown to enhance project organization, collaboration, and maintainability.

## Additional information
**Dataset**: Information on the datasets used in this tutorial is below:

* USGS Stream Gages (Real-time stream stage/water level):
    - Data Source: U.S. Geological Survey (USGS), [2024], USGS Water Data for the Nation: U.S. Geological Survey National Water Information System database, accessed [November 14, 2025], at https://doi.org/10.5066/F7P55KJN.
    - Access Software: `dataRetrieval`: R package for retrieving water data from US federal sources. U.S. Geological Survey Software Release. DOI: 10.32614/CRAN.package.dataRetrieval
        - Note that this workflow uses functions from the modern USGS Water API outlined here - https://water.code-pages.usgs.gov/dataRetrieval/articles/read_waterdata_functions.html/
* NWS Flooding Data (Flood Stage):
    - Data Source: U.S. National Water Prediction Service, National Oceanic and Atmospheric Administration. Real-time operational data accessed [November 14, 2025] at https://water.noaa.gov/, which is supported by the authoritative archived collection:
        - U.S. Department of Commerce, National Oceanic and Atmospheric Administration (NOAA), National Weather Service (DOC/NOAA/NWS). River Forecasts (Collection Period: 1873-07-01 to 1980-12-31). NOAA National Centers for Environmental Information (NCEI). [Accession Number: gov.noaa.ncdc:C00226]. Accessed [November 14, 2025] from: [https://www.ncei.noaa.gov/access/metadata/landing-page/bin/iso?id=gov.noaa.ncdc:C00226]
    - Access software: U.S. National Weather Service API. Retrieved from https://api.weather.gov/
        - GitHub link: https://github.com/weather-gov/api/
* NHC Hurricane Track (Hurricane Harvey):
    - Data Source: Official best track and intensity data for Hurricane Harvey (AL092017) accessed directly from the NOAA National Hurricane Center (NHC) - https://www.nhc.noaa.gov/data/, which is supported by the formal dataset citation:
        - Gahtan, Jennifer; Knapp, Kenneth R.; Schreck, Carl J. III; Diamond, Howard J.; Kossin, James P.; Kruk, Michael C. (2024). International Best Track Archive for Climate Stewardship (IBTrACS) Project, Version 4.01. Subset: North Atlantic basin (AL), 2017, Storm AL092017 – Hurricane Harvey. NOAA National Centers for Environmental Information. https://doi.org/10.25921/82ty-9e16 [November 14, 2025].

**Contact**: If you have any suggestion or report an issue with this notebook, feel free to [create an issue](https://github.com/alan-turing-institute/environmental-ds-book/issues/new/choose) or send a direct message to [environmental.ds.book@gmail.com](mailto:environmental.ds.book@gmail.com).

In [6]:
print(paste0('Last tested: ',Sys.Date()))

[1] "Last tested: 2025-09-26"
